In [1]:
import pandas as pd
import numpy as np
import nltk
import re
nltk.download('stopwords')
nltk.download('punkt')
nltk.download('wordnet')
from nltk.stem.snowball import SnowballStemmer
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords
wordnet = WordNetLemmatizer()
snowballstemmer = SnowballStemmer("english")
stopwords = stopwords.words('english')

from sklearn.feature_extraction.text import TfidfVectorizer
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer
from nltk.sentiment.util import *
from nltk import tokenize
sid = SentimentIntensityAnalyzer()

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/wangjiayun/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/wangjiayun/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/wangjiayun/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [64]:
biden = pd.read_csv("Biden_Tweets.csv")
biden = biden.dropna(subset=["Text"]).reset_index()

In [65]:
biden

index                       timestamp             Username  Retweets  \
0          0  Thu Apr 25 16:59:59 +0000 2019   980275870655893504         0   
1          1  Thu Apr 25 16:59:59 +0000 2019            102468365         0   
2          2  Thu Apr 25 16:59:58 +0000 2019   827325184432603136         0   
3          3  Thu Apr 25 16:59:57 +0000 2019   753734119893393408         0   
4          4  Thu Apr 25 16:59:57 +0000 2019            140074335         0   
5          5  Thu Apr 25 16:59:57 +0000 2019           2373123864         0   
6          6  Thu Apr 25 16:59:57 +0000 2019            493358463         0   
7          7  Thu Apr 25 16:59:57 +0000 2019             32987649         0   
8          8  Thu Apr 25 16:59:57 +0000 2019            221011668         1   
9          9  Thu Apr 25 16:59:55 +0000 2019           2269936974         0   
10        10  Thu Apr 25 16:59:54 +0000 2019            223526305         0   
11        11  Thu Apr 25 16:59:54 +0000 2019            235090920         1   
12        12  Thu Apr 25 16:59:52 +0000 2019             21733067         0   
13        13  Thu Apr 25 16:59:50 +0000 2019            564241606         0   
14        15  Thu Apr 25 16:59:50 +0000 2019             14299926         0   
15        16  Thu Apr 25 16:59:50 +0000 2019             14845337         0   
16        17  Thu Apr 25 16:59:50 +0000 2019             58005882         0   
17        18  Thu Apr 25 16:59:50 +0000 2019           2305740907         0   
18        19  Thu Apr 25 16:59:49 +0000 2019           2180056032         0   
19        20  Thu Apr 25 16:59:49 +0000 2019   799334252831801344         0   
20        21  Thu Apr 25 16:59:48 +0000 2019            466953226         2   
21        22  Thu Apr 25 16:59:48 +0000 2019             70751132         0   
22        23  Thu Apr 25 16:59:48 +0000 2019             15986096         0   
23        24  Thu Apr 25 16:59:48 +0000 2019            183554696         0   
24        25  Thu Apr 25 16:59:47 +0000 2019   958672653493194752         0   
25        26  Thu Apr 25 16:59:46 +0000 2019             52970736         0   
26        27  Thu Apr 25 16:59:46 +0000 2019             26928006        12   
27        28  Thu Apr 25 16:59:46 +0000 2019            309871944         0   
28        29  Thu Apr 25 16:59:45 +0000 2019             37947169         0   
29        30  Thu Apr 25 16:59:45 +0000 2019           2591357336         0   
...      ...                             ...                  ...       ...   
52374  52770  Sat Apr 11 11:49:45 +0000 2020  1058159518683672577         0   
52375  52771  Sat Apr 11 11:49:45 +0000 2020   824668403436773376         0   
52376  52772  Sat Apr 11 11:49:44 +0000 2020            145393538         0   
52377  52773  Sat Apr 11 11:49:44 +0000 2020           3318038060         0   
52378  52774  Sat Apr 11 11:49:44 +0000 2020             15956640         0   
52379  52775  Sat Apr 11 11:49:44 +0000 2020             17888709         0   
52380  52776  Sat Apr 11 11:49:44 +0000 2020           2788196223         0   
52381  52777  Sat Apr 11 11:49:44 +0000 2020   966716807452258304         0   
52382  52778  Sat Apr 11 11:49:43 +0000 2020             64425008         1   
52383  52779  Sat Apr 11 11:49:43 +0000 2020  1026958795178684417         0   
52384  52780  Sat Apr 11 11:49:43 +0000 2020  1242409082037944320         0   
52385  52781  Sat Apr 11 11:49:43 +0000 2020  1248738978200772608         0   
52386  52782  Sat Apr 11 11:49:42 +0000 2020   835888975487385600         0   
52387  52783  Sat Apr 11 11:49:42 +0000 2020   947508088306675712         0   
52388  52784  Sat Apr 11 11:49:42 +0000 2020  1087130417239650307         0   
52389  52785  Sat Apr 11 11:49:41 +0000 2020  1111397130005069829         0   
52390  52786  Sat Apr 11 11:49:40 +0000 2020  1178162222545166336         0   
52391  52787  Sat Apr 11 11:49:40 +0000 2020  1225155583705255938         0   
52392  52788  Sat Apr 11 11:49:39 +0000 2020            2

In [66]:
from unidecode import unidecode
from re import sub

def text_to_word_list(text, remove_polish_letters):
    ''' Pre process and convert texts to a list of words 
    method inspired by method from eliorc github repo: https://github.com/eliorc/Medium/blob/master/MaLSTM.ipynb'''
    text = remove_polish_letters(text)
    text = str(text)
    text = text.lower()

    # Clean the text
    text = sub(r"[^A-Za-z0-9^,!?.\/'+]", " ", text)
    text = sub(r"\+", " plus ", text)
    text = sub(r",", " ", text)
    text = sub(r"\.", " ", text)
    text = sub(r"!", " ", text)
    text = sub(r"\?", " ", text)
    text = sub(r"'", " ", text)
    text = sub(r":", " ", text)
    text = sub(r"\s{2,}", " ", text)
    text = sub(r'http\S+', '', text)

    text = text.split()
    text = list(filter(lambda x: len(x) > 1, text))

    return text  

In [67]:
biden["Cleaned_Text"] = biden["Text"].apply(lambda x: text_to_word_list(x, unidecode))

In [68]:
biden

index                       timestamp             Username  Retweets  \
0          0  Thu Apr 25 16:59:59 +0000 2019   980275870655893504         0   
1          1  Thu Apr 25 16:59:59 +0000 2019            102468365         0   
2          2  Thu Apr 25 16:59:58 +0000 2019   827325184432603136         0   
3          3  Thu Apr 25 16:59:57 +0000 2019   753734119893393408         0   
4          4  Thu Apr 25 16:59:57 +0000 2019            140074335         0   
5          5  Thu Apr 25 16:59:57 +0000 2019           2373123864         0   
6          6  Thu Apr 25 16:59:57 +0000 2019            493358463         0   
7          7  Thu Apr 25 16:59:57 +0000 2019             32987649         0   
8          8  Thu Apr 25 16:59:57 +0000 2019            221011668         1   
9          9  Thu Apr 25 16:59:55 +0000 2019           2269936974         0   
10        10  Thu Apr 25 16:59:54 +0000 2019            223526305         0   
11        11  Thu Apr 25 16:59:54 +0000 2019            235090920         1   
12        12  Thu Apr 25 16:59:52 +0000 2019             21733067         0   
13        13  Thu Apr 25 16:59:50 +0000 2019            564241606         0   
14        15  Thu Apr 25 16:59:50 +0000 2019             14299926         0   
15        16  Thu Apr 25 16:59:50 +0000 2019             14845337         0   
16        17  Thu Apr 25 16:59:50 +0000 2019             58005882         0   
17        18  Thu Apr 25 16:59:50 +0000 2019           2305740907         0   
18        19  Thu Apr 25 16:59:49 +0000 2019           2180056032         0   
19        20  Thu Apr 25 16:59:49 +0000 2019   799334252831801344         0   
20        21  Thu Apr 25 16:59:48 +0000 2019            466953226         2   
21        22  Thu Apr 25 16:59:48 +0000 2019             70751132         0   
22        23  Thu Apr 25 16:59:48 +0000 2019             15986096         0   
23        24  Thu Apr 25 16:59:48 +0000 2019            183554696         0   
24        25  Thu Apr 25 16:59:47 +0000 2019   958672653493194752         0   
25        26  Thu Apr 25 16:59:46 +0000 2019             52970736         0   
26        27  Thu Apr 25 16:59:46 +0000 2019             26928006        12   
27        28  Thu Apr 25 16:59:46 +0000 2019            309871944         0   
28        29  Thu Apr 25 16:59:45 +0000 2019             37947169         0   
29        30  Thu Apr 25 16:59:45 +0000 2019           2591357336         0   
...      ...                             ...                  ...       ...   
52374  52770  Sat Apr 11 11:49:45 +0000 2020  1058159518683672577         0   
52375  52771  Sat Apr 11 11:49:45 +0000 2020   824668403436773376         0   
52376  52772  Sat Apr 11 11:49:44 +0000 2020            145393538         0   
52377  52773  Sat Apr 11 11:49:44 +0000 2020           3318038060         0   
52378  52774  Sat Apr 11 11:49:44 +0000 2020             15956640         0   
52379  52775  Sat Apr 11 11:49:44 +0000 2020             17888709         0   
52380  52776  Sat Apr 11 11:49:44 +0000 2020           2788196223         0   
52381  52777  Sat Apr 11 11:49:44 +0000 2020   966716807452258304         0   
52382  52778  Sat Apr 11 11:49:43 +0000 2020             64425008         1   
52383  52779  Sat Apr 11 11:49:43 +0000 2020  1026958795178684417         0   
52384  52780  Sat Apr 11 11:49:43 +0000 2020  1242409082037944320         0   
52385  52781  Sat Apr 11 11:49:43 +0000 2020  1248738978200772608         0   
52386  52782  Sat Apr 11 11:49:42 +0000 2020   835888975487385600         0   
52387  52783  Sat Apr 11 11:49:42 +0000 2020   947508088306675712         0   
52388  52784  Sat Apr 11 11:49:42 +0000 2020  1087130417239650307         0   
52389  52785  Sat Apr 11 11:49:41 +0000 2020  1111397130005069829         0   
52390  52786  Sat Apr 11 11:49:40 +0000 2020  1178162222545166336         0   
52391  52787  Sat Apr 11 11:49:40 +0000 2020  1225155583705255938         0   
52392  52788  Sat Apr 11 11:49:39 +0000 2020            2

In [110]:
sentences = biden["Cleaned_Text"].apply(lambda x: " ".join(x))

In [130]:
def tokenization_and_stem(tokens):
    
    token_ls = []
    snowballstemmer_token_ls = []
    wordNet_token_ls = []
    for token in tokens:
        if token not in stopwords:
            token_ls.append(token)
            snowballstemmer_token_ls.append(snowballstemmer.stem(token))
            wordNet_token_ls.append(wordnet.lemmatize(token))
    
    return token_ls, snowballstemmer_token_ls, wordNet_token_ls


df_tweet = [0]*len(biden["Text"])
token_ls = [0]*len(biden["Text"])
snowstemmer_token_ls = [0]*len(biden["Text"])
wordNet_token_ls = [0]*len(biden["Text"])

for num, text in enumerate(biden["Cleaned_Text"]):
    token_ls[num], snowstemmer_token_ls[num] , wordNet_token_ls[num] = tokenization_and_stem(text)

In [132]:
snowstemmer_token_ls

[['presid', 'trump', 'thank'],
 ['pic', 'twitter', 'com/pxypfuzzdb'],
 ['hang', 'em', 'high', 'refer', 'less', 'subtl'],
 ['donald',
  'trump',
  'make',
  'joe',
  'biden',
  'point',
  'mock',
  'candid',
  'intellig',
  'dem',
  'sick',
  'de',
  '//www',
  'yahoo',
  'com/entertainment/donald',
  'trump',
  'make',
  'joe',
  'biden',
  '130340726',
  'html',
  'tsrc',
  'fauxdal'],
 ['factual',
  'speak',
  'accur',
  'trump',
  'accus',
  'near',
  'two',
  'dozen',
  'incid',
  'sexual',
  'misconduct',
  'includ',
  'rape',
  'one',
  'accus',
  'biden',
  'anyth',
  'sexual',
  'far',
  '//www',
  'businessinsid',
  'com/women',
  'accus',
  'trump',
  'sexual',
  'misconduct',
  'list',
  '2017',
  '12'],
 ['haaaaaa'],
 ['ask',
  'joe',
  'biden',
  'intellig',
  'presid',
  'sit',
  'white',
  'hous',
  'stupid',
  'grin',
  'face',
  'trump',
  'intellig',
  'presid',
  'yet'],
 ['us', 'peopl', 'elect', 'trump'],
 ['donald',
  'trump',
  'jr',
  'win',
  'internet',
  'thum

In [139]:
def back_to_clean_sent(token_ls):
    """
    In order to perform sentiment analysis,
    here we put the words back into sentences. 
    """
    
    clean_sent_ls = []
    for word_ls in token_ls:
        clean_sent = ""
        for word in word_ls:
            clean_sent += (word + " ")
        clean_sent_ls.append(clean_sent)
    return clean_sent_ls


sentence_tokenized = back_to_clean_sent(token_ls)
    
sentence_snowstemmeed = back_to_clean_sent(snowstemmer_token_ls)
    
sentence_wordnetstemmeed = back_to_clean_sent(wordNet_token_ls)


In [140]:
def sentiment_analysis(insert_processed_sentence):
    """
    Do the sentiment analysis!!
    """
    sentiment = [0]*len(biden["Text"])
    for num, player_sent in enumerate(insert_processed_sentence):
        ll = []
        for sentence in player_sent:
            ss = sid.polarity_scores(sentence)
            ll.append(ss)
        sentiment[num] = ll
    return sentiment


sentiment_original = sentiment_analysis(biden["Text"])
sentiment_token = sentiment_analysis(sentence_tokenized)
sentiment_snowstemmed = sentiment_analysis(sentence_snowstemmeed)

In [141]:
sentiment_token

[[{'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0},
  {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0},
  {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0},
  {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0},
  {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0},
  {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0},
  {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0},
  {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0},
  {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0},
  {'neg': 0.0, 'neu': 0.0, 'pos': 0.0, 'compound': 0.0},
  {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0},
  {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0},
  {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0},
  {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0},
  {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0},
  {'neg': 0.0, 'neu': 0.0, 'pos': 0.0, 'compound': 0.0},
  {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0},
  {'neg': 0.0, 'neu': 1.0, 'pos

In [ ]:
# Sentiment Analysis and create dataframe
new_df = pd.DataFrame()
i = 0
for senti_token, snow_stem in zip(sentiment_token, sentiment_snowstemmed):
    #senti_token_pos = [], senti_token_neu = [], senti_token_neg = []
    senti_token_compound = []
    senti_stem_compound = []
    sentiment_result_token = []
    sentiment_result_stem = []

    for s1 in senti_token:
        senti_token_compound.append(s1["compound"])
        if s1["compound"] >= 0.05:
            sentiment_result_token.append("positive")
        elif s1["compound"] <= -0.05:
            sentiment_result_token.append("negative")
        else:
            sentiment_result_token.append("neutral")
            
    for s2 in snow_stem:
        senti_stem_compound.append(s2["compound"])
        if s2["compound"] >= 0.05:
            sentiment_result_stem.append("positive")
        elif s2["compound"] <= -0.05:
            sentiment_result_stem.append("negative")
        else:
            sentiment_result_stem.append("neutral")
        
    tw_df = pd.DataFrame.from_dict({"Tweets":df["Tweets"][i],
                                "Create_time":df["Create_time"][i],
                                "Name":df["Name"][i],
                                "sentiment_token_compound":senti_token_compound,
                                "sentiment_result_token" :sentiment_result_token, 
                                "sentiment_stem_compound":senti_stem_compound,
                                "sentiment_result_stem":sentiment_result_stem})
    new_df = new_df.append(tw_df)
    i += 1
    

In [142]:
Tweets_mix = []
for i, row in enumerate(sentence_snowstemmeed):
    all_row = ""
    for sent in row:
        all_row += sent
    Tweets_mix.append(all_row)

In [17]:
Tweets_mix

['presid trump thank ',
 'pic twitter com/pxypfuzzdb ',
 'hang em high refer less subtl ',
 'donald trump make joe biden point mock candid intellig dem sick de //www yahoo com/entertainment/donald trump make joe biden 130340726 html tsrc fauxdal ',
 'factual speak accur trump accus near two dozen incid sexual misconduct includ rape one accus biden anyth sexual far //www businessinsid com/women accus trump sexual misconduct list 2017 12 ',
 'haaaaaa ',
 'ask joe biden intellig presid sit white hous stupid grin face trump intellig presid yet ',
 'us peopl elect trump ',
 'donald trump jr win internet thump creepi uncl joe biden big michael avenatti endors //www thegatewaypundit com/2019/04/donald trump jr win internet thump creepi uncl joe biden big michael avenatti endorsement/ via gatewaypundit ',
 'time run joe ',
 'care ',
 'tri get rid establish ruler ',
 'know biden knew was/i shame parent put pedo creep place offic would place dirti hand child real quick like camera camera ',
 '27

In [143]:
# create the TF-IDF matrix and model first
tfidf_model = TfidfVectorizer(max_df=0.8, max_features=2000,
                                 min_df=0.2, stop_words='english',
                                 use_idf=True, tokenizer=None, ngram_range=(1,1))

tfidf_matrix = tfidf_model.fit_transform(Tweets_mix) #fit the vectorizer to synopses

print ("In total, there are " + str(tfidf_matrix.shape[0]) + \
      " players and " + str(tfidf_matrix.shape[1]) + " terms.")

In total, there are 52404 players and 3 terms.


In [23]:
from sklearn.cluster import KMeans
num_clusters = 3
km = KMeans(n_clusters=num_clusters)
km.fit(tfidf_matrix)
clusters = km.labels_.tolist()

# create DataFrame films from all of the input files.
films = {'Name': biden["Username"].tolist(), 'Cluster': clusters}
frame = pd.DataFrame(films, index = [clusters])


l1, l2 = "", ""
for player in sentence_tokenized:
    for sent in player:
        l1 += sent
docs_tokenized = l1.split()

for player in sentence_snowstemmeed:
    for sent in player:
        l2 += sent
docs_snowstemmed = l2.split()

vocab_frame_dict = {docs_snowstemmed[x]:docs_tokenized[x] for x in range(len(docs_snowstemmed))}
tf_selected_words = tfidf_model.get_feature_names()

print ("Clustering result by K-means")
# km.cluster_centers_ denotes the importances of each items in centroid.
# We need to sort it in decreasing-order and get the top k items.
order_centroids = km.cluster_centers_.argsort()[:, ::-1] 

Cluster_keywords_summary = {}
for i in range(num_clusters):
    print ("Cluster " + str(i) + " words: ", end='')
    Cluster_keywords_summary[i] = []
    for ind in order_centroids[i, :3]: #replace 5 with n words per cluster
        Cluster_keywords_summary[i].append(vocab_frame_dict[tf_selected_words[ind]])
        print (vocab_frame_dict[tf_selected_words[ind]] + ",", end='')

    #cluster_NBA = frame.loc[i]['Name'].values
    #print("\n", ", ".join(cluster_NBA), "\n")

Clustering result by K-means
Cluster 0 words: joe,com,biden,Cluster 1 words: com,biden,joe,Cluster 2 words: biden,joe,com,

In [24]:
Cluster_keywords_summary

{0: ['joe', 'com', 'biden'],
 1: ['com', 'biden', 'joe'],
 2: ['biden', 'joe', 'com']}

In [148]:
frame.rename(columns = {"Name": "Username"}).merge(biden)

Username  Cluster  index                       timestamp  \
0        980275870655893504        0      0  Thu Apr 25 16:59:59 +0000 2019   
1                 102468365        1      1  Thu Apr 25 16:59:59 +0000 2019   
2        827325184432603136        0      2  Thu Apr 25 16:59:58 +0000 2019   
3        753734119893393408        2      3  Thu Apr 25 16:59:57 +0000 2019   
4                 140074335        1      4  Thu Apr 25 16:59:57 +0000 2019   
5                2373123864        0      5  Thu Apr 25 16:59:57 +0000 2019   
6                 493358463        2      6  Thu Apr 25 16:59:57 +0000 2019   
7                  32987649        0      7  Thu Apr 25 16:59:57 +0000 2019   
8                 221011668        2      8  Thu Apr 25 16:59:57 +0000 2019   
9                2269936974        2      9  Thu Apr 25 16:59:55 +0000 2019   
10                223526305        0     10  Thu Apr 25 16:59:54 +0000 2019   
11                235090920        0     11  Thu Apr 25 16:59:54 +0000 2019   
12                 21733067        2     12  Thu Apr 25 16:59:52 +0000 2019   
13                564241606        1     13  Thu Apr 25 16:59:50 +0000 2019   
14                 14299926        0     15  Thu Apr 25 16:59:50 +0000 2019   
15                 14845337        0     16  Thu Apr 25 16:59:50 +0000 2019   
16                 58005882        2     17  Thu Apr 25 16:59:50 +0000 2019   
17               2305740907        0     18  Thu Apr 25 16:59:50 +0000 2019   
18               2180056032        1     19  Thu Apr 25 16:59:49 +0000 2019   
19       799334252831801344        0     20  Thu Apr 25 16:59:49 +0000 2019   
20                466953226        2     21  Thu Apr 25 16:59:48 +0000 2019   
21                466953226        2   7051  Tue Jun 11 16:59:59 +0000 2019   
22                466953226        2     21  Thu Apr 25 16:59:48 +0000 2019   
23                466953226        2   7051  Tue Jun 11 16:59:59 +0000 2019   
24                 70751132        2     22  Thu Apr 25 16:59:48 +0000 2019   
25                 15986096        2     23  Thu Apr 25 16:59:48 +0000 2019   
26                183554696        1     24  Thu Apr 25 16:59:48 +0000 2019   
27       958672653493194752        0     25  Thu Apr 25 16:59:47 +0000 2019   
28       958672653493194752        0    937  Wed May 01 16:59:09 +0000 2019   
29       958672653493194752        0   1019  Wed May 01 16:56:42 +0000 2019   
...                     ...      ...    ...                             ...   
121258            237130212        0  52761  Sat Apr 11 11:49:53 +0000 2020   
121259   993870104373989377        1  52763  Sat Apr 11 11:49:51 +0000 2020   
121260           2772593255        0  52764  Sat Apr 11 11:49:50 +0000 2020   
121261  1025413008930025472        0  52766  Sat Apr 11 11:49:48 +0000 2020   
121262             27580422        2  52767  Sat Apr 11 11:49:48 +0000 2020   
121263             75423648        1  52768  Sat Apr 11 11:49:47 +0000 2020   
121264   952334937310494728        0  52769  Sat Apr 11 11:49:45 +0000 2020   
121265   824668403436773376        0  52771  Sat Apr 11 11:49:45 +0000 2020   
121266            145393538        2  52772  Sat Apr 11 11:49:44 +0000 2020   
121267           3318038060        0  52773  Sat Apr 11 11:49:44 +0000 2020   
121268             15956640        0  52774  Sat Apr 11 11:49:44 +0000 2020   
121269             17888709        2  52775  Sat Apr 11 11:49:44 +0000 2020   
121270           2788196223        2  52776  Sat Apr 11 11:49:44 +0000 2020   
121271   966716807452258304        0  52777  Sat Apr 11 11:49:44 +0000 2020   
121272             64425008        2  52778  Sat Apr 11 11:49:43 +0000 2020   
121273  1242409082037944320        0  52780  Sat Apr 11 11:49:43 +0000 2020   
121274  1248738978200772608        0  52781  Sat Apr 11 11:49:43 +0000 2020   
121275   835888975487385600        0  52782  Sat Apr 11 11:49:42 +0000 2020   
121276   947508088306675712        0  52783  Sat Apr 11 11:49:42 +000